## Scatter plot with `Scattertext`
`scattertext` is "a tool for finding distinguishing terms in small-to-medium-sized corpora, and presenting them in an interesting, interactive scatter plot with non-overlapping term labels." (See the [documentation]( https://github.com/JasonKessler/scattertext).)

In this notebook, we are going to compare the works of two 19th century novelists: [Charles Dickens](https://en.wikipedia.org/wiki/Charles_Dickens) and [George Eliot](https://en.wikipedia.org/wiki/George_Eliot) (aka Mary Ann Evans). Such a comparison could be used to address questions about gender when it comes to authorship, or, perhaps, about key differences between novels set in urban vs. rural environments.

## Set up

In [1]:
!pip install scattertext

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.2/8.2 MB 19.8 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.4/9.4 MB 29.6 MB/s eta 0:00:0000:0100:01
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.9/233.9 kB 21.9 MB/s eta 0:00:00
  Created wheel for flashtext: filename=flashtext-2.7-py2.py3-none-any.whl size=9297 sha256=e9a099b0985c1812814828137b8e8d820eec960c269563bccebc1ec6a9faa284
  Stored in directory: /Users/chloethurmgreene/Library/Caches/pip/wheels/49/20/47/f03dfa8a7239c54cbc44ff7389eefbf888d2c1873edaaec888
Successfully built flashtext


In [2]:
import pandas as pd
import scattertext as st
from IPython.core.display import HTML

In [3]:
#load data
dickens_url = 'https://raw.githubusercontent.com/msaxton/nlp-data/main/dickens.csv'
dickens_df = pd.read_csv(dickens_url)

In [5]:
# sanity check
print(dickens_df.shape)
dickens_df.sample(5)

(24707, 6)


author        title  \
9411   dickens  copperfield   
22756  dickens     pickwick   
16832  dickens        bleak   
23866  dickens     pickwick   
13225  dickens  copperfield   

                                                    text  \
9411   ‘Here! Peggotty!’ cried Miss Betsey, opening t...   
22756  'It's not so much that, Mr. Weller,' replied M...   
16832   “But I know she is very beautiful this morning.”   
23866  'Well, I think he was; I think I may say he wa...   
13225  He looked upon her, while she made this suppli...   

                           nouns              adjectives  \
9411           door tea mistress   parlour little unwell   
22756                       wine         much bad afraid   
16832                    morning               beautiful   
23866  man story uncle gentleman                    same   
13225        supplication manner  wild distracted silent   

                                          verbs  
9411                            cry open dawdle  
22756                           reply dissipate  
16832                                      know  
23866  think think say answer eye tell surprise  
13225                           look make raise

In [6]:
#load data
eliot_url = 'https://raw.githubusercontent.com/msaxton/nlp-data/main/eliot.csv'
eliot_df = pd.read_csv(eliot_url)

In [7]:
# sanity check
print(eliot_df.shape)
eliot_df.sample(5)

(18139, 6)


author        title                                               text  \
13382  eliot       romola  “There you go, supposing you’ll get people to ...   
8443   eliot      deronda  It happened that the very vividness of his imp...   
9816   eliot      deronda  “If he were here again, what should I do? I ca...   
3348   eliot  middlemarch  “People will not make a boast of being methodi...   
1989   eliot  middlemarch  “People don’t like his religious tone,” said L...   

                                                   nouns  \
13382  people leg sack pair hosen beast man battle fi...   
8443   vividness impression friend indefiniteness sen...   
9816                face coward contempt fiend will face   
3348                                  People boast while   
1989                                         People tone   

                                              adjectives  \
13382                                       wild unarmed   
8443   enigmatic apparent many sided persistent memor...   
9816                                    dead beggar dead   
3348                                  methodistical good   
1989                                           religious   

                                                   verbs  
13382  go suppose get put call say say rush ’ run fac...  
8443   happen make contribute waken develop threaten ...  
9816   wish bear bear go go wander stay feel turn bea...  
3348                                           make come  
1989                                      like say break

## Pre-process data

There are a few changes we need to make to our data to get it ready for processing by `Scattertext`.

**First**, we are going to get a smaller sample of the data so that we can process things more quickly for our in-class demonstration. If you were to do this as a research project, you might consider using your entire dataset.

**Second**, we are going to combine both datasets into one `DataFrame`.

**Third**, we are going to drop all the columns from that `DataFrame` except for `author` and `nouns.`

In [8]:
# create samples
dickens_sample_df = dickens_df.sample(10_000)
eliot_sample_df = eliot_df.sample(10_000)

In [9]:
# combine DataFrames
df = pd.concat([dickens_sample_df, eliot_sample_df])

In [10]:
# drop all columns except 'author' and 'nouns'
nouns_df = df[['author', 'nouns']]

In [12]:
# sanity check
print(nouns_df.shape)
nouns_df.sample(10)

(20000, 2)


author                                              nouns
6524   dickens  doctor day sake sex mood fellow compassion fel...
10029  dickens                               voice judge question
4621     eliot  sob minute house attic floor head worm shelf s...
14533    eliot         pity falsehood sort shrug time side affair
6033   dickens                            candle table book night
8048     eliot                                        layer thing
18732  dickens  step room trifling indication room darkness wa...
7686     eliot  credit sake kind idiot brace passport life uni...
705      eliot             haunt pleasure footprint echo treasure
12934  dickens     turn room love wife self inclination head door

## Build corpus and visualize

Now that we have our data in the shape that we need, we can hand it over to `Scattertext` to do the heavy lifting. The code below follows `Scattertext`'s [documentation](https://github.com/JasonKessler/scattertext). We first create a `Scattertext` corpus, then we transform that corpus into an html-based visualization, finally, we display that visualization within our notebook. Note: you can also download the visualization as an html file.

In [13]:
# create a scattertext corpus
corpus = st.CorpusFromPandas(nouns_df, category_col='author', text_col='nouns').build()

In [14]:
# transform corpus into html-based visualization with scattertext
html = st.produce_scattertext_explorer(corpus,
                                       category='eliot',  # this sets the y-axis
                                       category_name='Eliot', # label y-axis
                                       not_category_name='Dickens',  # label x-axis
                                       minimum_term_frequency=20,
                                       width_in_pixels=900)

In [15]:
# display visualization in notebook
HTML(html)

In [16]:
# Note: You can save this visualization as an html file
file_name = 'inclass_corpus.html'
with open(file_name, encoding='utf8', mode='w') as f:
    f.write(html)

## Compare using adjectives

We have compared Dickens and Eliot on the basis of the nouns they used. It might also be infomrative to compare them on the basis of the adjectives they used.

Starting with our initial datasets, `dickens_df` and `eliot_df`, make a comparison on the adjectives used by these authors using `Scattertext`.

In [17]:
# create samples
dickens_sample_df2 = dickens_df.sample(10_000)
eliot_sample_df2 = eliot_df.sample(10_000)

In [18]:
# combine DataFrames
df2 = pd.concat([dickens_sample_df2, eliot_sample_df2])

In [19]:
# drop all columns except 'author' and 'adjectives'
adj_df = df2[['author', 'adjectives']]

In [21]:
# create a scattertext corpus
corpus = st.CorpusFromPandas(adj_df, category_col='author', text_col='adjectives').build()

In [22]:
# # transform corpus into html-based visualization with scattertext
html = st.produce_scattertext_explorer(corpus,
                                       category='eliot',  # this sets the y-axis
                                       category_name='Eliot', # label y-axis
                                       not_category_name='Dickens',  # label x-axis
                                       minimum_term_frequency=20,
                                       width_in_pixels=900)

In [23]:
# display visualization in notebook
HTML(html)

In [24]:
# Note: You can save this visualization as an html file
file_name = 'HW_corpus.html'
with open(file_name, encoding='utf8', mode='w') as f:
    f.write(html)